<a href="https://colab.research.google.com/github/ManukyanErik/Implements/blob/main/Neural%20Network/Cifar_10_Recognition_in_Images.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# [CIFAR-10 - Object Recognition in Images](https://www.kaggle.com/competitions/cifar-10/leaderboard)

In [28]:
import pandas as pd
import numpy as np

# from sklearn.model_selection import train_test_split

from keras.models import Sequential
#Import from keras_preprocessing not from keras.preprocessing
from keras_preprocessing.image import ImageDataGenerator
from keras.layers import Dense, Activation, Flatten, Dropout, BatchNormalization
from keras.layers import Conv2D, MaxPooling2D
from keras import regularizers, optimizers

In [29]:
import zipfile

zip_files = ['test', 'train']

for zip_file in zip_files:
    with zipfile.ZipFile("/content/drive/MyDrive/Colab Notebooks/Projects/Cifar-10/{}.zip".format(zip_file),"r") as z:
        z.extractall(".")
        print("{} unzipped".format(zip_file))


test unzipped
train unzipped


In [30]:
traindf=pd.read_csv("/content/drive/MyDrive/Colab Notebooks/Projects/Cifar-10/trainLabels.csv", dtype=str)
testdf=pd.read_csv("/content/drive/MyDrive/Colab Notebooks/Projects/Cifar-10/sampleSubmission.csv",dtype=str)


def append_ext(fn):
    return fn+".png"

traindf["id"]=traindf["id"].apply(append_ext)
testdf["id"]=testdf["id"].apply(append_ext)


In [31]:
datagen=ImageDataGenerator(rescale=1./255.,validation_split=0.25)
train_generator=datagen.flow_from_dataframe(dataframe=traindf,
                                            directory="./train/",
                                            x_col="id",
                                            y_col="label",
                                            subset="training",
                                            batch_size=32,
                                            seed=42,
                                            shuffle=True,
                                            class_mode="categorical",
                                            target_size=(32,32))

valid_generator=datagen.flow_from_dataframe(dataframe=traindf,
                                            directory="./train/",
                                            x_col="id",
                                            y_col="label",
                                            subset="validation",
                                            batch_size=32,
                                            seed=42,
                                            shuffle=True,
                                            class_mode="categorical",
                                            target_size=(32,32))


test_datagen=ImageDataGenerator(rescale=1./255.)
test_generator=test_datagen.flow_from_dataframe(dataframe=testdf,
                                                directory="./test/",
                                                x_col="id",
                                                y_col=None,
                                                batch_size=32,
                                                seed=42,
                                                shuffle=False,
                                                class_mode=None,
                                                target_size=(32,32))

Found 37500 validated image filenames belonging to 10 classes.
Found 12500 validated image filenames belonging to 10 classes.
Found 300000 validated image filenames.


In [35]:
model = Sequential()
model.add(Conv2D(32, (3, 3), padding='same',input_shape=(32,32,3)))
model.add(Activation('relu'))
model.add(Conv2D(32, (3, 3)))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))
model.add(Conv2D(64, (3, 3), padding='same'))
model.add(Activation('relu'))
model.add(Conv2D(64, (3, 3)))
model.add(Activation('relu'))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(512))
model.add(Activation('relu'))
model.add(Dropout(0.5))
model.add(Dense(10, activation='softmax'))

model.compile(optimizer= "adam" , # optimizers.rmsprop(lr=0.0001, decay=1e-6),
              loss="categorical_crossentropy",
              metrics=["accuracy"])

In [36]:
STEP_SIZE_TRAIN=train_generator.n//train_generator.batch_size
STEP_SIZE_VALID=valid_generator.n//valid_generator.batch_size
STEP_SIZE_TEST=test_generator.n//test_generator.batch_size

model.fit_generator(generator=train_generator,
                    steps_per_epoch=STEP_SIZE_TRAIN,
                    validation_data=valid_generator,
                    validation_steps=STEP_SIZE_VALID,
                    epochs=10)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:9: UserWarning: `Model.fit_generator` is deprecated and will be removed in a future version. Please use `Model.fit`, which supports generators.
  if __name__ == '__main__':


Epoch 1/10
1171/1171 [==============================] - 35s 19ms/step - loss: 1.5951 - accuracy: 0.4140 - val_loss: 1.2278 - val_accuracy: 0.5610
Epoch 2/10
1171/1171 [==============================] - 18s 16ms/step - loss: 1.2426 - accuracy: 0.5570 - val_loss: 1.0596 - val_accuracy: 0.6214
Epoch 3/10
1171/1171 [==============================] - 18s 15ms/step - loss: 1.0694 - accuracy: 0.6200 - val_loss: 0.9126 - val_accuracy: 0.6754
Epoch 4/10
1171/1171 [==============================] - 18s 15ms/step - loss: 0.9548 - accuracy: 0.6605 - val_loss: 0.8625 - val_accuracy: 0.6972
Epoch 5/10
1171/1171 [==============================] - 22s 19ms/step - loss: 0.8715 - accuracy: 0.6925 - val_loss: 0.8223 - val_accuracy: 0.7133
Epoch 6/10
1171/1171 [==============================] - 18s 15ms/step - loss: 0.8118 - accuracy: 0.7141 - val_loss: 0.7920 - val_accuracy: 0.7195
Epoch 7/10
1171/1171 [==============================] - 20s 17ms/step - loss: 0.7686 - accuracy: 0.7299 - val_loss: 0.7852 -

In [39]:
model.evaluate_generator(generator=valid_generator, steps=STEP_SIZE_TEST)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: UserWarning: `Model.evaluate_generator` is deprecated and will be removed in a future version. Please use `Model.evaluate`, which supports generators.
  """Entry point for launching an IPython kernel.


[0.7106699347496033, 0.7529600262641907]

In [40]:
test_generator.reset()
pred = model.predict_generator(test_generator, steps=STEP_SIZE_TEST, verbose=1)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: UserWarning: `Model.predict_generator` is deprecated and will be removed in a future version. Please use `Model.predict`, which supports generators.
  after removing the cwd from sys.path.


9375/9375 [==============================] - 154s 16ms/step


In [41]:
predicted_class_indices = np.argmax(pred,axis=1)

In [43]:
labels = (train_generator.class_indices)
labels = dict((v,k) for k,v in labels.items())
predictions = [labels[k] for k in predicted_class_indices]

In [56]:
# filenames=test_generator.filenames
# results=pd.DataFrame({"id":filenames,
#                       "label":predictions})

# results.to_csv("results.csv",index=False)

In [59]:
ids = list(range(1, len(predictions)+1))
df = pd.DataFrame({"id":ids,'label': predictions})

# import the modules we'll need
from IPython.display import HTML
import pandas as pd
import numpy as np
import base64

# function that takes in a dataframe and creates a text link to  
# download it (will only work for files < 2MB or so)
def create_download_link(df, title = "Download CSV file", filename = "data.csv"):  
    csv = df.to_csv(index = False)
    b64 = base64.b64encode(csv.encode())
    payload = b64.decode()
    html = '<a download="{filename}" href="data:text/csv;base64,{payload}" target="_blank">{title}</a>'
    html = html.format(payload=payload,title=title,filename=filename)
    return HTML(html)


create_download_link(df)